In [1]:
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch import optim
import math, copy, time
from torch.autograd import Variable
import matplotlib.pyplot as plt
from IPython.display import Image
import pandas as pd
import re
import jieba
from torchtext import data,datasets
import random
import os
from tqdm import tqdm
from torchtext.data import Iterator,BucketIterator
from torchtext.vocab import Vectors
from torch.nn import LSTM,LSTMCell,Linear
from transformers import *
import tokenize
import json

/root/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/root/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/root/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/root/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: P

In [2]:
#使用transformers中的模型加载，需要将bert_config.json 重命名为config.json
bert_model=BertModel.from_pretrained('./bert_pretrain/')
tokenizer = BertTokenizer.from_pretrained("./bert_pretrain/")

I0426 02:04:16.138382 140389550884608 configuration_utils.py:148] loading configuration file ./bert_pretrain/config.json
I0426 02:04:16.139438 140389550884608 configuration_utils.py:168] Model config {
  "attention_probs_dropout_prob": 0.1,
  "directionality": "bidi",
  "finetuning_task": null,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 1024,
  "initializer_range": 0.02,
  "intermediate_size": 4096,
  "is_decoder": false,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "num_attention_heads": 16,
  "num_hidden_layers": 3,
  "num_labels": 2,
  "output_attentions": false,
  "output_hidden_states": false,
  "output_past": true,
  "pooler_fc_size": 768,
  "pooler_num_attention_heads": 12,
  "pooler_num_fc_layers": 3,
  "pooler_size_per_head": 128,
  "pooler_type": "first_token_transform",
  "pruned_heads": {},
  "torchscript": false,
  "type_vocab_size": 2,
  "use_bfloat16": false,
  "vocab_size": 21128
}

I0426 02:04:16.141477 140389550884608 mode

In [3]:
BATCH_SIZE=16
CT_MAX_LEN=400
Q_MAX_LEN=100
A_MAX_LEN=10

In [4]:
train_path='./data/train_data.csv'
test_path='./data/train_test.csv'
dev_path='./data/train_dev.csv'

In [5]:
def build_dataset():
    pad_idx=0
    def padcontext(context):
        if len(context)>CT_MAX_LEN:
            context=context[:CT_MAX_LEN]
        else:
            context += [pad_idx for i in range(CT_MAX_LEN - len(context))]
        return context
        
    def padq(question):
        if len(question)>Q_MAX_LEN:
            question=question[:Q_MAX_LEN]
        else:
            question += [pad_idx for i in range(Q_MAX_LEN - len(question))]
        return question
    
    def pada(answer):
        if len(answer)>A_MAX_LEN:
            answer=answer[:A_MAX_LEN]
        else:
            answer += [pad_idx for i in range(A_MAX_LEN - len(answer))]
        return answer
    
    def load_train_dataset(path,num):
        contents = []
        csv_data=pd.read_csv(path,lineterminator='\n')
        i=0
        for id,question,context,answer,answer_start in zip(csv_data['id'],csv_data['question'],csv_data['context'],csv_data['answer'],csv_data['answer_start']):
            if len(context)>400:
                continue
            q_token=tokenizer.tokenize(question)
            q_token_ids=tokenizer.convert_tokens_to_ids(q_token)
            len_q=len(q_token_ids)
#             q_tokenids=padq(q_token_ids)
            
            c_token=tokenizer.tokenize(str(context))
            c_token_ids=tokenizer.convert_tokens_to_ids(c_token)
            len_c=len(c_token_ids)
#             c_tokenids=padcontext(c_token_ids)
            
            a_token=tokenizer.tokenize(str(answer))
            a_token_ids=tokenizer.convert_tokens_to_ids(a_token)
            len_a=len(a_token_ids)
            a_tokenids=pada(a_token_ids)
            
            answer_end=int(answer_start)+len_a
            contents.append((q_token_ids,c_token_ids,a_tokenids,len_q,len_c,len_a,answer_start,answer_end,c_token,id,a_token))
            if num!=0:
                i+=1
                if i>num:
                    break
        return contents
    
    def load_dev_dataset(path,num):
        contents = []
        csv_data=pd.read_csv(path,lineterminator='\n')
        i=0
        for id,question,context,answer in zip(csv_data['id'],csv_data['question'],csv_data['context'],csv_data['answer']):
            if len(context)>400:
                continue
            q_token=tokenizer.tokenize(question)
            q_token_ids=tokenizer.convert_tokens_to_ids(q_token)
            len_q=len(q_token_ids)
#             q_tokenids=padq(q_token_ids)
            
            c_token=tokenizer.tokenize(str(context))
            c_token_ids=tokenizer.convert_tokens_to_ids(c_token)
            len_c=len(c_token_ids)
#             c_tokenids=padcontext(c_token_ids)
    
            contents.append((q_token_ids,c_token_ids,len_q,len_c,c_token,answer,id))
            if num!=0:
                i+=1
                if i>num:
                    break
        return contents
            
    train = load_train_dataset(train_path,num=0)
    dev = load_dev_dataset(dev_path,num=0)
    return train, dev

In [6]:
class DatasetIterater(object):
    def __init__(self, dataset, batch_size, device):
        self.batch_size = batch_size
        self.dataset = dataset
        self.n_batches = len(dataset) // batch_size
        self.residue = False  # 记录batch数量是否为整数
        if len(dataset) % self.n_batches != 0:
            self.residue = True
        self.index = 0
        self.device = device
    
    def _to_tensor(self, datas):
        
        
        c_lens = [len(s[1]) for s in datas]
#         c_pad = torch.zeros(len(datas), max(c_lens)).long()
        c_pad = torch.zeros(len(datas), CT_MAX_LEN).long()
        for i, inp in enumerate(datas):
            c=inp[1]
            end = c_lens[i]
            c_pad[i, :end] = torch.LongTensor(c[end-1::-1])
            
        q_lens = [len(s[0]) for s in datas]
#         q_pad = torch.zeros(len(datas), max(q_lens)).long()
        q_pad = torch.zeros(len(datas), Q_MAX_LEN).long()
        for i, inp in enumerate(datas):
            q=inp[0]
            end = q_lens[i]
            q_pad[i, :end] = torch.LongTensor(q[end-1::-1])
        
        c_pad=c_pad.to(self.device)
        q_pad=q_pad.to(self.device)
#         q = torch.LongTensor([_[0] for _ in datas]).to(self.device)
#         c = torch.LongTensor([_[1] for _ in datas]).to(self.device)
        a = torch.LongTensor([_[2] for _ in datas]).to(self.device)

        # pad前的长度(超过pad_size的设为pad_size)
        q_len = torch.LongTensor([_[3] for _ in datas]).to(self.device)
        c_len = torch.LongTensor([_[4] for _ in datas]).to(self.device)
        a_len = torch.LongTensor([_[5] for _ in datas]).to(self.device)
        a_start = torch.LongTensor([_[6] for _ in datas]).to(self.device)
        a_end = torch.LongTensor([_[7] for _ in datas]).to(self.device)
        c_token=[_[8] for _ in datas]
        id=[_[9] for _ in datas]
        a_token=[_[10] for _ in datas]
        return (q_pad, c_pad, a,q_len,c_len,a_len,a_start,a_end,c_token,id,a_token)

    def __next__(self):
        if self.residue and self.index == self.n_batches:
            batches = self.dataset[self.index * self.batch_size: len(self.dataset)]
            self.index += 1
            batches = self._to_tensor(batches)
            return batches

        elif self.index >= self.n_batches:
            self.index = 0
            raise StopIteration
        else:
            batches = self.dataset[self.index * self.batch_size: (self.index + 1) * self.batch_size]
            self.index += 1
            batches = self._to_tensor(batches)
            return batches

    def __iter__(self):
        return self

    def __len__(self):
        if self.residue:
            return self.n_batches + 1
        else:
            return self.n_batches
        
class DevDatasetIterater(object):
    def __init__(self, dataset, batch_size, device):
        self.batch_size = batch_size
        self.dataset = dataset
        self.n_batches = len(dataset) // batch_size
        self.residue = False  # 记录batch数量是否为整数
        if len(dataset) % self.n_batches != 0:
            self.residue = True
        self.index = 0
        self.device = device

    def _to_tensor(self, datas):
        c_lens = [len(s[1]) for s in datas]
#         c_pad = torch.zeros(len(datas), max(c_lens)).long()
        c_pad = torch.zeros(len(datas), CT_MAX_LEN).long()
        for i, inp in enumerate(datas):
            c=inp[1]
            end = c_lens[i]
            c_pad[i, :end] = torch.LongTensor(c[end-1::-1])
            
        q_lens = [len(s[0]) for s in datas]
#         q_pad = torch.zeros(len(datas), max(q_lens)).long()
        q_pad = torch.zeros(len(datas), Q_MAX_LEN).long()
        for i, inp in enumerate(datas):
            q=inp[0]
            end = q_lens[i]
            q_pad[i, :end] = torch.LongTensor(q[end-1::-1])
        
        c=c_pad.to(self.device)
        q=q_pad.to(self.device)
        
#         print(datas)
#         q = torch.LongTensor([_[0] for _ in datas]).to(self.device)
#         c = torch.LongTensor([_[1] for _ in datas]).to(self.device)
 
        # pad前的长度(超过pad_size的设为pad_size)
        q_len = torch.LongTensor([_[2] for _ in datas]).to(self.device)
        c_len = torch.LongTensor([_[3] for _ in datas]).to(self.device)
        c_token=[_[4] for _ in datas]
        answer=[_[5] for _ in datas]
        id=[_[6] for _ in datas]
        return (q, c,q_len,c_len,c_token,answer,id)

    def __next__(self):
        if self.residue and self.index == self.n_batches:
            batches = self.dataset[self.index * self.batch_size: len(self.dataset)]
            self.index += 1
            batches = self._to_tensor(batches)
            return batches

        elif self.index >= self.n_batches:
            self.index = 0
            raise StopIteration
        else:
            batches = self.dataset[self.index * self.batch_size: (self.index + 1) * self.batch_size]
            self.index += 1
            batches = self._to_tensor(batches)
            return batches

    def __iter__(self):
        return self

    def __len__(self):
        if self.residue:
            return self.n_batches + 1
        else:
            return self.n_batches
        
def build_iterator(dataset,data_type,batch_size,device):
    if data_type=='train':
        iter = DatasetIterater(dataset, batch_size, device)
    else:
        iter = DevDatasetIterater(dataset, batch_size, device)

    return iter

In [7]:
#Batch构造函数的输入是src和trg，后者可以为None，因为再预测的时候是没有tgt的。
class Batch:
    def __init__(self, batch,data_type):
        if data_type=='train':
            self.pad=0
            self.q = batch[0]
            self.c=batch[1]
            self.q_mask = (batch[0] != self.pad)
            self.c_mask=(batch[1]!=self.pad)
            self.a=batch[2]
            self.a_mask=(batch[2]!=self.pad)
            self.q_len=batch[3]
            self.c_len=batch[4]
            self.a_len=batch[5]
            self.a_start=batch[6]
            self.a_end=batch[7]
            self.c_token=batch[8]
            self.id=batch[9]
            self.a_token=batch[10]
        else:
            self.pad=0
            self.q = batch[0]
            self.c=batch[1]
            self.q_mask = (batch[0] != self.pad)
            self.c_mask=(batch[1]!=self.pad)
            self.q_len=batch[2]
            self.c_len=batch[3]
            self.c_token=batch[4]
            self.answers=batch[5]
            self.id=batch[6]
            
         
    
def rebatch(batch,data_type):
    return Batch(batch,data_type)

# 定义模型

In [8]:

'''
在每两个子层之间都使用了残差连接(Residual Connection) 和归一化。
'''

# 归一化层
class LayerNorm(nn.Module):
    "构造一个 layernorm 模块 (See citation for details)."
    def __init__(self, features, eps=1e-6):
        super(LayerNorm, self).__init__()
        self.a_2 = nn.Parameter(torch.ones(features))
        self.b_2 = nn.Parameter(torch.zeros(features))
        self.eps = eps

    def forward(self, x):
        mean = x.mean(-1, keepdim=True)
        std = x.std(-1, keepdim=True)
        return self.a_2 * (x - mean) / (std + self.eps) + self.b_2
    
 #为了能方便地使用这些残差连接，模型中所有的子层和Embedding层的输出都设定成了相同的维度，即d_model=512
# 封装残差连接和归一化，便于代码复用
class SublayerConnection(nn.Module):
    """
     LayerNorm + sublayer(Self-Attenion/Dense) + dropout + 残差连接
     为了简单，把LayerNorm放到了前面，这和原始论文稍有不同，原始论文LayerNorm在最后。
    """
    def __init__(self, size, dropout):
        super(SublayerConnection, self).__init__()
        self.norm = LayerNorm(size)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x, sublayer):
        #"sublayer是传入的参数，参考DecoderLayer，它可以当成函数调用，这个函数的有一个输入参数"
        return x + self.dropout(sublayer(self.norm(x)))
    
def clones(module, N):
    "生成N个完全一样的层."
    return nn.ModuleList([copy.deepcopy(module) for _ in range(N)])
def attention(query, key, value, mask=None, dropout=None):
    d_k = query.size(-1)
    scores = torch.matmul(query, key.transpose(-2, -1)) / math.sqrt(d_k)

#     print('attention scores.size:',scores.size())
#     print('attention mask.size:',mask.size())
    if mask is not None:
        scores = scores.masked_fill(mask == 0, -1e9)
        
    p_attn = F.softmax(scores, dim = -1)
    if dropout is not None:
        p_attn = dropout(p_attn)
    return torch.matmul(p_attn, value), p_attn

class MultiHeadedAttention(nn.Module):
    def __init__(self, h, d_model, dropout=0.1):
        "Take in model size and number of heads."
        super(MultiHeadedAttention, self).__init__()
        assert d_model % h == 0
        # W我们假设d_v总是等于d_k
        self.d_k = d_model // h
        self.h = h
        self.linears = clones(nn.Linear(d_model, d_model), 4)
        self.attn = None
        self.dropout = nn.Dropout(p=dropout)
        
    def forward(self, query, key, value, mask=None):
        
        if mask is not None:
#             print('mask1.size:',mask.size())
            mask=mask.unsqueeze(-2)
#             print('mask2.size:',mask.size())
            # 所有h个head的mask都是相同的
            mask = mask.unsqueeze(1)
        nbatches = query.size(0)
        
        # 1) 首先使用线性变换，然后把d_model分配给h个Head，每个head为d_k=d_model/h 
        query, key, value = [l(x).view(nbatches, -1, self.h, self.d_k).transpose(1, 2) 
                             for l, x in zip(self.linears, (query, key, value))]
#         print('query.size:',query.size())
#         print('key.size:',key.size())
#         print('value.size:',value.size())
        # 2) 使用attention函数计算,x的shape是(batch, 8, time, 64)，而attn是(batch, 8, time, time)。
        x, self.attn = attention(query, key, value, mask=mask, 
                                 dropout=self.dropout)
        
        # 3) 把8个head的64维向量拼接成一个512的向量。然后再使用一个线性变换(512,521)，shape不变。 
        x = x.transpose(1, 2).contiguous().view(nbatches, -1, self.h * self.d_k)
        return self.linears[-1](x)

#全连接子层，全连接层的输入和输出都是d_model(512)维的，中间隐单元的个数是d_ff(2048)。
class PositionwiseFeedForward(nn.Module):
    def __init__(self, d_model, d_ff, dropout=0.1):
        super(PositionwiseFeedForward, self).__init__()
        self.w_1 = nn.Linear(d_model, d_ff)
        self.w_2 = nn.Linear(d_ff, d_model)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        #在两个线性变换之间除了ReLu还使用了一个Dropout。
        return self.w_2(self.dropout(F.relu(self.w_1(x))))
#Embeddings，这里除了使用Embedding外还* math.sqrt(self.d_model)
class Embeddings(nn.Module):
    def __init__(self, d_model, vocab):
        super(Embeddings, self).__init__()
        self.lut = nn.Embedding(vocab, d_model)
        self.d_model = d_model

    def forward(self, x):
        return self.lut(x) * math.sqrt(self.d_model)

#位置编码
# 假设输入是ID序列长度为10，如果输入Embedding之后是(10, 512)，那幺位置编码的输出也是(10, 512)。
# 上式中pos就是位置(0-9)，512维的偶数维使用sin函数，而奇数维使用cos函数。
class PositionalEncoding(nn.Module):
    def __init__(self, d_model, dropout, max_len=5000):
        super(PositionalEncoding, self).__init__()
        self.dropout = nn.Dropout(p=dropout)
        
        pe = torch.zeros(max_len, d_model)
        position = torch.arange(0., max_len).unsqueeze(1)
        div_term = torch.exp(torch.arange(0., d_model, 2) *
                             -(math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        pe = pe.unsqueeze(0)
        
        # register_buffer通常用于保存一些模型参数之外的值，它不是模型的参数(不用梯度下降)，但是模型会修改它，
        # 而且在预测的时候也要使用它。这里也是类似的，pe是一个提前计算好的常量，我们在forward要用到它。
        # 我们在构造函数里并没有把pe保存到self里，但是在forward的时候我们却可以直接使用它(self.pe)。
        self.register_buffer('pe', pe)
        
    def forward(self, x):
        x = x + Variable(self.pe[:, :x.size(1)], 
                         requires_grad=False)
        return self.dropout(x)

In [9]:
def make_model(src_vocab, tgt_vocab, N=6, 
               d_model=512, d_ff=2048, h=8, dropout=0.1):
    c = copy.deepcopy
    attn = MultiHeadedAttention(h, d_model)
    ff = PositionwiseFeedForward(d_model, d_ff, dropout)
    position = PositionalEncoding(d_model, dropout)
    model = EncoderDecoder(
        Encoder(EncoderLayer(d_model, c(attn), c(ff), dropout), N),
        Decoder(DecoderLayer(d_model, c(attn), c(attn), c(ff), dropout), N),
        nn.Sequential(Embeddings(d_model, src_vocab), c(position)),
        nn.Sequential(Embeddings(d_model, tgt_vocab), c(position)),
        Generator(d_model, tgt_vocab))
    
    # 随机初始化参数，这非常重要
    for p in model.parameters():
        if p.dim() > 1:
            nn.init.xavier_uniform(p)
    return model

In [10]:
#初始化lstm模型的参数
def init_lstm_wt(lstm):
    for names in lstm._all_weights:
        for name in names:
            if name.startswith('weight_'):
                wt = getattr(lstm, name)
                wt.data.uniform_(-0.02, 0.02)
            elif name.startswith('bias_'):
                # set forget bias to 1
                bias = getattr(lstm, name)
                n = bias.size(0)
                start, end = n // 4, n // 2
                bias.data.fill_(0.)
                bias.data[start:end].fill_(1.)

In [11]:
class EncoderLayer(nn.Module):
    def __init__(self, size, self_attn, feed_forward, dropout):
        super(EncoderLayer, self).__init__()
        self.self_attn = self_attn
        self.feed_forward = feed_forward
        self.sublayer = clones(SublayerConnection(size, dropout), 2)
        self.size = size
  
    def forward(self, x, mask):
        # MultiAtention->Add&Norm
        x = self.sublayer[0](x, lambda x: self.self_attn(x, x, x, mask))
        
        # FeedForward-》Add&Norm
        return self.sublayer[1](x, self.feed_forward)

class Encoder(nn.Module):
    def __init__(self,bert,emb_dim,hidden_dim):
        super(Encoder, self).__init__()
        
        self.pre_model=bert
        self.hidden_dim=hidden_dim
        for param in self.pre_model.parameters():
            param.requires_grad = False
        
        self.lstm = nn.LSTM(1024, hidden_dim, num_layers=3,
                            bidirectional=True, batch_first=True)

        self.W_h = nn.Linear(hidden_dim * 2, hidden_dim * 2, bias=False)
        self.dropout=0.1
        self.c = copy.deepcopy
        self.attn = MultiHeadedAttention(8, hidden_dim)
        self.ff = PositionwiseFeedForward(hidden_dim, 2048,  self.dropout)
        self.position = PositionalEncoding(hidden_dim, self.dropout)
        self.linear=nn.Linear(1024,hidden_dim, bias=False)
        self.emb=nn.Sequential(self.linear, self.c(self.position))
        self.sublayer=clones(SublayerConnection(hidden_dim,  self.dropout), 2)
        self.N=6
        self.layer=EncoderLayer(hidden_dim, self.c(self.attn), self.c(self.ff), self.dropout)
        self.layers = clones(self.layer, self.N)
        self.norm = LayerNorm(self.layer.size)
        
    #seq_lens should be in descending order
    def forward(self, input_q, input_mask,input_lens):
        print('input_q.size:',input_q.size())
        encoder_out, text_cls = self.pre_model(input_q, attention_mask=input_mask)
        print('encoder_out11 size:',encoder_out.size())
        x = self.emb(encoder_out)
        print('x.size:',x.size())
        for i in self.layers:
            x = self.layer(x, input_mask)
         
        encoder_out=self.norm(x)
    
        print('encoder_out size:',encoder_out.size())
        #pack_padded_sequence 去除pad；lengths需要从大到小排序，batch_first如果设置为true，则x的第一维为batch_size，第二维为seq_length，否则相反。
#         encoder_outputs, hidden = self.lstm(encoder_out)
#         print('encoder_outs size:',encoder_outputs.size())

#         print(hidden[0].size(),hidden[1].size())

#         encoder_out = self.W_h(encoder_out)
        
        return encoder_out

In [12]:
class Decoder(nn.Module):
     def __init__(self,bert,emb_dim,hidden_dim):
        super(Encoder, self).__init__()
        
        self.pre_model=bert
        self.hidden_dim=hidden_dim
        for param in self.pre_model.parameters():
            param.requires_grad = True
        
        self.lstm = nn.LSTM(emb_dim, hidden_dim, num_layers=1, batch_first=True, bidirectional=True)
        
        init_lstm_wt(self.lstm)

        self.p_gen_linear = nn.Linear(hidden_dim * 4 + emb_dim, 1)
        self.x_context = nn.Linear(hidden_dim * 2 + emb_dim, emb_dim)
        self.ac_attention=ACAttention()
        self.ac_att_linear=nn.Linear()

        
     #seq_lens should be in descending order
     def forward(self, input_a, a_mask,input_lens,encoder_outputs, encoder_feature, enc_padding_mask,c_t_1,s_t,qc_attn):
        a_encoder_out, text_cls = self.pre_model(input_a, attention_mask=a_mask)

        #拼接decoder输入与（encoder输出attention后的值）
        x = self.x_context(torch.cat((c_t_1, a_encoder_out), 1))
        
        lstm_out, s_t = self.lstm(x.unsqueeze(1), s_t_1)
        h_decoder, c_decoder = s_t
        s_t_hat = torch.cat((h_decoder.view(-1, self.hidden_dim),
                             c_decoder.view(-1, self.hidden_dim)), 1)  # B x 2*hidden_dim
        c_t, attn_dist = self.attention_network(s_t_hat, encoder_outputs, encoder_feature,enc_padding_mask)
        qc_attn=qc_attn.sequeeze()
        
        

In [13]:
class PointerDecoder(nn.Module):
     def __init__(self,hidden_size,dropout):
        super(PointerDecoder, self).__init__()
        
        # 5. Modeling Layer
        self.modeling_LSTM1 = LSTM(input_size=hidden_size * 3, #*6
                                   hidden_size=hidden_size,
                                   bidirectional=True,
                                   batch_first=True,
                                   dropout=dropout)
        init_lstm_wt(self.modeling_LSTM1)


        self.modeling_LSTM2 = LSTM(input_size=hidden_size *2,
                                   hidden_size=hidden_size,
                                   bidirectional=True,
                                   batch_first=True,
                                   dropout=dropout)
        init_lstm_wt(self.modeling_LSTM2)


        # 6. Output Layer
        self.p1_weight_g = Linear(hidden_size * 3, 1) #*6
        self.p1_weight_m = Linear(hidden_size * 2 , 1)
        self.p2_weight_g = Linear(hidden_size * 3, 1) #*6
        self.p2_weight_m = Linear(hidden_size * 2, 1)
        
        self.output_LSTM = LSTM(input_size=hidden_size * 2,
                                hidden_size=hidden_size,
                                bidirectional=True,
                                batch_first=True,
                                dropout=dropout)
        init_lstm_wt(self.output_LSTM)


     #seq_lens should be in descending order
     def forward(self, attn,c_lens):
        m = self.modeling_LSTM2((self.modeling_LSTM1(attn)[0]))[0]
        # (batch, c_len)
        p1 = (self.p1_weight_g(attn) + self.p1_weight_m(m)).squeeze()
        # (batch, c_len, hidden_size * 2)
        m2 = self.output_LSTM(m)[0]
        # (batch, c_len)
        p2 = (self.p2_weight_g(attn) + self.p2_weight_m(m2)).squeeze()
        return p1, p2 
        
        

In [14]:
class QCAttention(nn.Module):
    def __init__(self,hidden_dim):
        super(QCAttention, self).__init__()
        self.att_weight_c = Linear(hidden_dim , 1)
        self.att_weight_q = Linear(hidden_dim , 1)
        self.att_weight_cq = Linear(hidden_dim , 1)

    def qc_attention(self,q_encoder_feature,c_encoder_feature,c_len,q_len,q_mask,c_mask):
        q_mask = q_mask.unsqueeze(1)
        c_mask = c_mask.unsqueeze(1)
        
        
        key=torch.cat([c_encoder_feature,q_encoder_feature],dim=1)
        query=key
        d_k = query.size(-1)
        scores = torch.matmul(query, key.transpose(-2, -1)) / math.sqrt(d_k)

        cq_attn = F.softmax(scores, dim = -1)        
        cq_attn=cq_attn[:,:c_len,c_len:]  #batch*c_len*q_len
        print('cq_attn',cq_attn.size())
        cq_attn = cq_attn.masked_fill(q_mask == 0, -1e9) # batch*c_len*q_len
        normalization_factor = cq_attn.sum(1, keepdim=True)
        cq_attn = cq_attn / normalization_factor
        
        #value:batch*q_len*(2*hidden)
        cq_weight=torch.matmul(cq_attn, q_encoder_feature)  #batch*c_len*(2*hidden)
        
        qc_attn = F.softmax(torch.max(cq_attn, dim=2)[0], dim=1).unsqueeze(1)
        print('qc_attn',qc_attn.size())
        
#         qc_attn = qc_attn.masked_fill(c_mask == 0, -1e9)
        # (batch, 1, c_len) * (batch, c_len, hidden_size * 2) -> (batch, hidden_size * 2)
        qc_weight = torch.bmm(qc_attn, c_encoder_feature).squeeze()
        # (batch, c_len, hidden_size * 2) (tiled)
        qc_weight = qc_weight.unsqueeze(1).expand(-1, c_len, -1)
        # p_attn=p_attn.permute(0,2,1)
        # p_attn= F.max_pool1d(p_attn,kernel_size=1,stride=1)

        
        
        x=torch.cat([qc_weight,cq_weight,c_encoder_feature],dim=-1)
        print('QCAttention x.size==',x.size())
        return x

    def att_flow_layer(self,q,c):
        """
          param c: (batch, c_len, hidden_size * 2)
          param q: (batch, q_len, hidden_size * 2)
          return: (batch, c_len, q_len)
        """
        c_len=c.size(1)
        q_len=q.size(1)
        cq=[]
        for i in range(q_len):
            qi=q.select(1,i).unsqueeze(1) #(batch,1,hidden_size*2)
            ci=self.att_weight_cq(c*qi).squeeze() # #(batch, c_len, 1)
            cq.append(ci)
        #(batch,c_len,q_len) 
        cq=torch.stack(cq,dim=-1)
        #(batch,c_len,q_len)
        s = self.att_weight_c(c).expand(-1, -1, q_len) + \
                self.att_weight_q(q).permute(0, 2, 1).expand(-1, c_len, -1) + \
                cq

        # (batch, c_len, q_len)
        a = F.softmax(s, dim=2)
        # (batch, c_len, q_len) * (batch, q_len, hidden_size * 2) -> (batch, c_len, hidden_size * 2)
        c2q_att = torch.bmm(a, q)
        # (batch, 1, c_len)
        b = F.softmax(torch.max(s, dim=2)[0], dim=1).unsqueeze(1)
        # (batch, 1, c_len) * (batch, c_len, hidden_size * 2) -> (batch, hidden_size * 2)
        q2c_att = torch.bmm(b, c).squeeze()
        # (batch, c_len, hidden_size * 2) (tiled)
        q2c_att = q2c_att.unsqueeze(1).expand(-1, c_len, -1)
        # q2c_att = torch.stack([q2c_att] * c_len, dim=1)

        # (batch, c_len, hidden_size * 8)
        x = torch.cat([c, c2q_att, c * c2q_att, c * q2c_att], dim=-1)
        return x
        
            
    
    def forward(self, q_encoder_feature, c_encoder_feature, q_mask, c_mask):
       
        x=self.qc_attention(q_encoder_feature,c_encoder_feature,c_encoder_feature.size(1),
                                           q_encoder_feature.size(1),q_mask,c_mask)
#         x=self.att_flow_layer(q_encoder_feature,c_encoder_feature)
        return  x

In [15]:
class PointerNetLoss(nn.Module):
    def __init__(self):
        super(PointerNetLoss, self).__init__()

    def forward(self, target, logits, lengths):
        """
        Args:
          target : label data (bz, tgt_max_len)
          logits : predicts (bz, tgt_max_len, src_max_len)
          lengths : length of label data (bz)
        """
        _, tgt_max_len = target.size()
        logits_flat = logits.view(-1, logits.size(-1))
        log_logits_flat = torch.log(logits_flat)
        target_flat = target.view(-1, 1)
        losses_flat = -torch.gather(log_logits_flat, dim=1, index = target_flat)
        losses = losses_flat.view(*target.size())
        mask = sequence_mask(lengths, tgt_max_len)
        mask = Variable(mask)
        losses = losses * mask.float()
        loss = losses.sum() / lengths.float().sum()
        return loss

In [16]:
class EncoderDecoder(nn.Module):
    def __init__(self,bert,hidden_dim,emb_dim,dropout):
        super(EncoderDecoder,self).__init__()
        
        self.encoder=Encoder(bert,emb_dim,hidden_dim)
        self.decoder=PointerDecoder(hidden_dim,dropout)
        self.attention=QCAttention(hidden_dim)
        self.hidden_dim=hidden_dim
        
    def forward(self,batch):
        # 题目encoder
        q_encoder_outputs=self.encoder(batch.q,batch.q_mask,batch.q_len)
    
        #文章encoder
        c_encoder_outputs=self.encoder(batch.c,batch.c_mask,batch.c_len)
    
        #题目对文章注意,文章对题目注意
#         x=self.attention(q_encoder_feature,c_encoder_feature,batch.q_mask,batch.c_mask)
        x=self.attention(q_encoder_outputs,c_encoder_outputs,batch.q_mask,batch.c_mask)


        p1,p2=self.decoder(x,batch.c_len)
        return p1,p2
    

In [17]:
class EMA():
    def __init__(self, mu):
        self.mu = mu
        self.shadow = {}

    def register(self, name, val):
        self.shadow[name] = val.clone()

    def get(self, name):
        return self.shadow[name]

    def update(self, name, x):
        assert name in self.shadow
        new_average = (1.0 - self.mu) * x + self.mu * self.shadow[name]
        self.shadow[name] = new_average.clone()

In [18]:
from collections import OrderedDict
import io
import json
import six
import sys
if six.PY2:
    reload(sys)
    sys.setdefaultencoding('utf8')
import argparse


def _tokenize_chinese_chars(text):
    """
    :param text: input text, unicode string
    :return:
        tokenized text, list
    """

    def _is_chinese_char(cp):
        """Checks whether CP is the codepoint of a CJK character."""
        # This defines a "chinese character" as anything in the CJK Unicode block:
        #     https://en.wikipedia.org/wiki/CJK_Unified_Ideographs_(Unicode_block)
        #
        # Note that the CJK Unicode block is NOT all Japanese and Korean characters,
        # despite its name. The modern Korean Hangul alphabet is a different block,
        # as is Japanese Hiragana and Katakana. Those alphabets are used to write
        # space-separated words, so they are not treated specially and handled
        # like the all of the other languages.
        if ((cp >= 0x4E00 and cp <= 0x9FFF) or  #
            (cp >= 0x3400 and cp <= 0x4DBF) or  #
            (cp >= 0x20000 and cp <= 0x2A6DF) or  #
            (cp >= 0x2A700 and cp <= 0x2B73F) or  #
            (cp >= 0x2B740 and cp <= 0x2B81F) or  #
            (cp >= 0x2B820 and cp <= 0x2CEAF) or
            (cp >= 0xF900 and cp <= 0xFAFF) or  #
            (cp >= 0x2F800 and cp <= 0x2FA1F)):  #
            return True

        return False

    output = []
    buff = ""
    for char in text:
        cp = ord(char)
        if _is_chinese_char(cp) or char == "=":
            if buff != "":
                output.append(buff)
                buff = ""
            output.append(char)
        else:
            buff += char

    if buff != "":
        output.append(buff)

    return output


def _normalize(in_str):
    """
    normalize the input unicode string
    """
    in_str = in_str.lower()
    sp_char = [
        u':', u'_', u'`', u'，', u'。', u'：', u'？', u'！', u'(', u')',
        u'“', u'”', u'；', u'’', u'《', u'》', u'……', u'·', u'、', u',',
        u'「', u'」', u'（', u'）', u'－', u'～', u'『', u'』', '|'
    ]
    out_segs = []
    for char in in_str:
        if char in sp_char:
            continue
        else:
            out_segs.append(char)
    return ''.join(out_segs)


def find_lcs(s1, s2):
    """find the longest common subsequence between s1 ans s2"""
    m = [[0 for i in range(len(s2)+1)] for j in range(len(s1)+1)]
    max_len = 0
    p = 0
    for i in range(len(s1)):
        for j in range(len(s2)):
            if s1[i] == s2[j]:
                m[i+1][j+1] = m[i][j]+1
                if m[i+1][j+1] > max_len:
                    max_len = m[i+1][j+1]
                    p = i+1
    return s1[p-max_len:p], max_len


def evaluate(ref_ans, pred_ans):
    """
    ref_ans: reference answers, dict
    pred_ans: predicted answer, dict
    return:
        f1_score: averaged F1 score
        em_score: averaged EM score
        total_count: number of samples in the reference dataset
        skip_count: number of samples skipped in the calculation due to unknown errors
    """
    f1 = 0
    em = 0
    total_count = 0
    skip_count = 0
    for answers,prediction in zip(ref_ans,pred_ans):
        answers=eval(str(answers))
        _f1 = calc_f1_score(answers, prediction)
        f1 += _f1
        em += calc_em_score(answers, prediction)
        total_count+=1
        print("origin: {}".format('#'.join(answers)))
        print("pred: {}".format(prediction))
        print("score: {}".format(_f1))
        print('----------------------------')

    f1_score = 100.0 * f1 / total_count
    em_score = 100.0 * em / total_count
    return f1_score, em_score, total_count


def calc_f1_score(answers, prediction):
    f1_scores = []
    for ans in answers:
        ans_segs = _tokenize_chinese_chars(_normalize(ans))
        prediction_segs = _tokenize_chinese_chars(_normalize(prediction))

        lcs, lcs_len = find_lcs(ans_segs, prediction_segs)
        if lcs_len == 0:
            f1_scores.append(0)
            continue
        prec = 1.0*lcs_len/len(prediction_segs)
        rec = 1.0*lcs_len/len(ans_segs)
        f1 = (2 * prec * rec) / (prec + rec)
        f1_scores.append(f1)
    return max(f1_scores)


def calc_em_score(answers, prediction):
    em = 0
    for ans in answers:
        ans_ = _normalize(ans)
        prediction_ = _normalize(prediction)
        if ans_ == prediction_:
            em = 1
            break
    return em

In [19]:
import os
os.environ['CUDA_LAUNCH_BLOCKING'] = "1"

In [20]:
def test(model, ema, data_iter,criterion):
    loss = 0
    answers = dict()
    model.eval()
    ref_ans=[]
    pred_ans=[]
    backup_params = EMA(0)
    for name, param in model.named_parameters():
        if param.requires_grad:
            backup_params.register(name, param.data)
            param.data.copy_(ema.get(name))

    with torch.set_grad_enabled(False):
        for i, batch in enumerate(data_iter):
            batch=rebatch(batch,'dev')
            p1, p2 =  model.forward(batch)
#             print('p1.size:',p1.size())
#             print('p2.size:',p2.size())
#             print('p1:',p1)
#             print('p1:',p2)
#             batch_loss = criterion(p1, batch.a_start) + criterion(p2, batch.a_end)
#             loss += batch_loss.item()

            # (batch, c_len, c_len)
           
            batch_size, c_len = p1.size()
            ls = nn.LogSoftmax(dim=1)
            mask = (torch.ones(c_len, c_len) * float('-inf')).to(1).tril(-1).unsqueeze(0).expand(batch_size, -1, -1)
            score = (ls(p1).unsqueeze(2) + ls(p2).unsqueeze(1)) + mask
            score, s_idx = score.max(dim=1)
            score, e_idx = score.max(dim=1)
            print('s_idx:',s_idx)
            print('e_idx:',e_idx)
            s_idx = torch.gather(s_idx, 1, e_idx.view(-1, 1)).squeeze()
#             print('s_idx:',s_idx)
            for i in range(batch_size):
#                 tokenizer.convert_tokens_to_ids(batch.a_token)
                id = batch.id[i]
                answer = batch.c_token[i][s_idx[i]:e_idx[i]]
                
                answer = ''.join(answer)     
                pred_ans.append(answer)
                ref_ans.append(batch.answers[i])
                print('pre answer is :',answer)
                print('batch.answers is:',batch.answers[i])
                
                answers[id] = answer

        for name, param in model.named_parameters():
            if param.requires_grad:
                param.data.copy_(backup_params.get(name))

    with open('predict_result.txt', 'w', encoding='utf-8') as f:
        print(json.dumps(answers), file=f)

    f1_score, em_score, total_count = evaluate(ref_ans, pred_ans)
    return loss, f1_score, em_score


In [21]:
# "标准的训练和记录函数"
def run_epoch(data_iter, model,optimizer,criterion,ema,loss):
    start = time.time()
    total_tokens = 0
    total_loss = 0
    tokens = 0
    
    for i, batch in enumerate(data_iter):
        batch=rebatch(batch,'train')
        p1,p2 = model.forward(batch)
        optimizer.zero_grad()
        
        batch_loss = criterion(p1, batch.a_start) + criterion(p2, batch.a_end)
        loss += batch_loss.item()
        batch_loss.backward()
        optimizer.step()
        for name, param in model.named_parameters():
            if param.requires_grad:
                ema.update(name, param.data)          
    return loss

train_dataset,dev_dataset=build_dataset()
print(len(train_dataset),len(dev_dataset))

hidden_dim=256
emb_dim=128    
dropout=0.5
def train():
    learning_rate=0.005
    model=EncoderDecoder(bert_model,hidden_dim,emb_dim,dropout)
    model.to(1)
    ema = EMA(0.999)
    for name, param in model.named_parameters():
        if param.requires_grad:
            ema.register(name, param.data)
    parameters = filter(lambda p: p.requires_grad, model.parameters())
    optimizer = optim.Adadelta(parameters, lr=learning_rate)
    criterion = nn.CrossEntropyLoss()
    loss=0
    em_dev_exact, max_dev_f1 = -1, -1
    i=0
    for epoch in range(10):
        train_iter=build_iterator(train_dataset,'train',BATCH_SIZE,1)
        dev_iter=build_iterator(dev_dataset,'dev',BATCH_SIZE,1)

        loss=run_epoch(train_iter,model,optimizer,criterion,ema,loss)
        
        i+=1
        print("Epoch Step: %d Loss: %s " % (i, str(loss)))
        eval_loss, f1_score, em_score=test(model, ema, dev_iter,criterion) 
        print('eval_loss:',eval_loss)
        print('f1_score:',f1_score)
        print('em_score:',em_score)
        if f1_score > max_dev_f1:
            max_dev_f1 = f1_score
            max_dev_exact = em_score
            best_model = copy.deepcopy(model)

        loss = 0
        model.train()
        
    torch.save(best_model.state_dict(), f'./best_model.pt')
    

11622 1143


In [22]:
train()

/root/anaconda3/lib/python3.6/site-packages/torch/nn/modules/rnn.py:46: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.5 and num_layers=1
  "num_layers={}".format(dropout, num_layers))


input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100,

encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])

encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])

encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
input_q.size: torch.Size([16, 100])
encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])

...

encoder_out11 size: torch.Size([16, 100, 1024])
x.size: torch.Size([16, 100, 256])
encoder_out size: torch.Size([16, 100, 256])
input_q.size: torch.Size([16, 400])
encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
s_idx: tensor([[ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  1,  2,  ..., 12, 12, 12],
        [ 0,  0,  2,  ..., 11, 11, 11],
        ...,
        [ 0,  0,  0,  ..., 11, 11, 11],
        [ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  0,  0,  ...,  0,  0,  0]], device='cuda:1')
e_idx: tensor([ 9, 16, 29, 15, 10,  4, 17,  6,  5,  8, 10,  4,  6, 18,  7,  6],
       device='cuda:1')
pre answer is : t##p-link路由器的初
batch.answers is: ['admin']
pre answer is : 温度的，
batch.answers is: ['没有固定温度']
pre answer is : 皮带的时间要求都不一致，普遍在6万至
batch.answers is: ['6万至10万公里']
pre answer is : 上市的问题总结
batch.answe

encoder_out11 size: torch.Size([16, 400, 1024])
x.size: torch.Size([16, 400, 256])
encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
s_idx: tensor([[ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  0,  0,  ...,  9,  9,  9],
        [ 0,  0,  0,  ...,  9,  9,  9],
        ...,
        [ 0,  0,  0,  ..., 10, 10, 10],
        [ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  0,  0,  ...,  0,  0,  0]], device='cuda:1')
e_idx: tensor([ 9, 17, 14,  4,  5,  9,  8, 15,  9, 10, 17, 16,  9, 14,  5, 18],
       device='cuda:1')
pre answer is : 市场上的防腐木用材
batch.answers is: ['1800-2000左右', '1800-2000']
pre answer is : 2022年09月10日-2022
batch.answers is: ['2022年09月10日-2022年09月25日']
pre answer is : 于6000米的只
batch.answers is: ['11034米', '11034']
pre answer is : 小马真名
batch.answers is: ['马彦毅']
pre answer is : 小猫咪出生
batch.answers is: ['出生一个月后']
pre answer is : googlemap只适合在美国有
batch.answers is: ['Sygic']


encoder_out size: torch.Size([16, 400, 256])
cq_attn torch.Size([16, 400, 100])
qc_attn torch.Size([16, 1, 400])
QCAttention x.size== torch.Size([16, 400, 768])
s_idx: tensor([[ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  0,  0,  ...,  0,  0,  0],
        ...,
        [ 0,  0,  0,  ...,  0,  0,  0],
        [ 0,  0,  2,  ..., 13, 13, 13],
        [ 0,  0,  0,  ...,  0,  0,  0]], device='cuda:1')
e_idx: tensor([15, 16, 16,  4,  6, 98,  8, 16,  5,  8,  3,  4, 98, 12, 22, 29],
       device='cuda:1')
pre answer is : 据悉,《寒武纪》由周雨彤、侯明
batch.answers is: ['5月8日24点', '每周二至周五']
pre answer is : 油钱6000(算一年1##w公里,每公里大
batch.answers is: ['约等于2W', '2W']
pre answer is : 小黄鸭很不错啊～喜欢你点映137##8万
batch.answers is: ['2.7亿']
pre answer is : 女警手长
batch.answers is: ['女警']
pre answer is : 空中客车a3##80
batch.answers is: ['555名', '555']
pre answer is : 生产日期pd即product##iondate有效期gp即g##ua##rant##eepe##rio##d生产日期是指商品在生产线上完成所有工序，经过检验并包装成为可在市场上销售的成品时的日期和时间。有效期是指在规定的贮藏条件下质量能够符合规定要求的

score: 0
----------------------------
origin: 应付账款周转天数=360/应付账款周转率
pred: 成本/应
score: 0.09523809523809523
----------------------------
origin: 100万以上
pred: 殊要求的烘干场所
score: 0
----------------------------
origin: 11%
pred: 务总局关于
score: 0
----------------------------
origin: 麦顿金典天然粮
pred: 麦顿金典
score: 0.7272727272727273
----------------------------
origin: 至少8000万到9000万之间#至少8000万到9000万
pred: 有人统计过，饿死了至少8000万到9000
score: 0.5714285714285714
----------------------------
origin: 农村商业银行#信用社银行
pred: 农村信用社
score: 0.6
----------------------------
origin: 没有具体的分数线
pred: 考分数线+80分。若
score: 0.39999999999999997
----------------------------
origin: 1070万
pred: 巴巴成功登陆纽交
score: 0
----------------------------
origin: 238.03美元
pred: 表现受到市
score: 0
----------------------------
origin: 极速前进第三季
pred: 《极速前进第三季》是
score: 0.9333333333333333
----------------------------
origin: 6个
pred: 长春市现辖
score: 0
----------------------------
origin: 五年之后
pred: 法:无法清除,必
score: 0
----------------------------
origin: 奔腾E8700
pred:

pred: 空中客车a3##80
score: 0
----------------------------
origin: GP
pred: 生产日期pd即product##iondate有效期gp即g##ua##rant##eepe##rio##d生产日期是指商品在生产线上完成所有工序，经过检验并包装成为可在市场上销售的成品时的日期和时间。有效期是指在规定的贮藏条件下质量能够符合规定要求的期限。
score: 0.023255813953488372
----------------------------
origin: 魅蓝note3
pred: 魅蓝note##3性价比更
score: 0.4
----------------------------
origin: 2017年7月7日
pred: 《加勒比海盗5》原计划定于2015年7
score: 0.2
----------------------------
origin: 十一章
pred: 剑灵主线任
score: 0
----------------------------
origin: 高德#高德地图
pred: 高德是中国领先的
score: 0.4
----------------------------
origin: 飞利浦
pred: oled电视
score: 0
----------------------------
origin: 464医院
pred: 46##4医院
score: 0.6666666666666666
----------------------------
origin: 下周
pred: 青年节啊海贼王漫画86##4话什么时候更新86##4话情报剧情预测&#58##94##2;&#58##94##3;来源：闽南网发布：2017-05-0209:21:01五一长假在日本也是黄金周放假的时候，所以《海贼王》漫画下一话86##4话将在下周更新，
score: 0.05633802816901409
----------------------------
origin: 0.27—0.4mm
pred: 生长速度头发是毛发中生长
score: 0
----------------------------
origin: 150-280元左右#150-28